In [2]:
import requests
import os
import csv

metadata_endpoint = "https://graph.mapillary.com"

# Define bounding box center and distances to get an area to download from 
x_dist = 0.050
y_dist = 0.050
testpoint = [52.0881575, 5.1143055]  # Example: Center point

client_token = 'MLY|8196090173836012|99bcaed29312ec0d1c06b22447943d94'  # Your token 

headers = {"Authorization": "OAuth {}".format(client_token)}

# Construct the image search URL with the bounding box
url_imagesearch = metadata_endpoint + '/images?fields=id,location&bbox={}, {}, {}, {}'.format(
    testpoint[1] - x_dist, testpoint[0] - y_dist,
    testpoint[1] + x_dist, testpoint[0] + y_dist
)

# Request to search for images
response_imagesearch = requests.get(url_imagesearch, headers=headers)
data_imagesearch = response_imagesearch.json()

print("Images found: " + str(len(data_imagesearch['data'])))

# Create a directory to save images if it doesn't exist
os.makedirs('mapillary_images_with_orientation', exist_ok=True)

# Prepare a CSV file to save image metadata
csv_file_path = 'mapillary_images_with_orientation/metadata.csv'
with open(csv_file_path, mode='w', newline='') as csv_file:
    fieldnames = ['id', 'thumb_2048_url', 'captured_at', 'sequence', 'lat', 'long', 'orientation']
    writer = csv.DictWriter(csv_file, fieldnames=fieldnames)
    writer.writeheader()  # Write the header row

    for image in data_imagesearch['data']:
        # Fetch detailed information for each image
        url_image = metadata_endpoint + '/{}?fields=id,thumb_2048_url,captured_at,sequence,geometry,compass_angle'.format(image['id'])
        response_image = requests.get(url_image, headers=headers)
        data_image = response_image.json()

        # Print image data (for debugging)
        print(data_image)

        # Extract information
        img_id = data_image.get('id')
        img_url = data_image.get('thumb_2048_url')
        captured_at = data_image.get('captured_at')
        sequence = data_image.get('sequence')
        location = data_image.get('geometry')
        orientation = data_image.get('compass_angle')
        # Extract coordinates and orientation
        if location:
            coordinates = location.get('coordinates')
            if coordinates:
                longitude = coordinates[0]
                latitude = coordinates[1]
            else:
                longitude = None
                latitude = None

        else:
            longitude = None
            latitude = None

        # Save image metadata to CSV
        writer.writerow({
            'id': img_id,
            'thumb_2048_url': img_url,
            'captured_at': captured_at,
            'sequence': sequence,
            'lat': latitude,
            'long': longitude,
            'orientation': orientation  
        })

        # Download the image and save it to the local directory
        if img_url:
            img_response = requests.get(img_url)
            if img_response.status_code == 200:
                # Save the image with its ID as the filename
                img_filename = f'mapillary_images_with_orientation/{img_id}.jpg'
                with open(img_filename, 'wb') as f:
                    f.write(img_response.content)
                print(f'Downloaded {img_id}.jpg')
            else:
                print(f'Failed to download image {img_id}.jpg')
        else:
            print(f'No URL found for image {img_id}')


Images found: 2000
{'id': '1355293608185005', 'thumb_2048_url': 'https://scontent-ams2-1.xx.fbcdn.net/m1/v/t6/An8k4IUsceezFnUMlUFqXrhyWm8XXidAOYaV-C9TaHMoq_R0Bo3hePT2Hr20TjY_ErVzW7y3AHIKsHgxrH6kSoZkB_QGEjsAYKTuSmW8PS2EhIPhNizOBJ_B_bvO6AQAiom3q12iYEpNO_mdTBOAA_o?stp=s2048x1228&ccb=10-5&oh=00_AYB9Lzd-yDZ20Z2t6aha9XmHbLaQ5vUyf2mlwWBWL_Llow&oe=67327792&_nc_sid=201bca', 'captured_at': 1546348643572, 'sequence': 'A3FKFBudQCGMQJinvgTSnw', 'geometry': {'type': 'Point', 'coordinates': [5.1213266666667, 52.056625]}, 'compass_angle': 109.89992781901}
Downloaded 1355293608185005.jpg
{'id': '1442608966076135', 'thumb_2048_url': 'https://scontent-ams2-1.xx.fbcdn.net/m1/v/t6/An_wfod6draOJWsppBR5X4piksbUs3fq3eda_yZqmYCeKcACcVJ54ko9K8y9pI3SRGKJM6CLdATwUexFTm_SAut5h9o3zAjorCts06vpTUdiCaSFu0r8EToqx9nLr83I7DSmmT8ettZhGWBFKaMO4O4?stp=s2048x1536&ccb=10-5&oh=00_AYAwuq_ZpvrZ6_JmKrZGYLZ0vkW3sPgxgBOrL8441dY2Qw&oe=67328407&_nc_sid=201bca', 'captured_at': 1457797275448, 'sequence': 'zDV0VquOoKyRDCVBiPOOmA', 'geom

In [5]:
import pandas as pd
import folium
from IPython.display import display

# Load the metadata from the CSV file
csv_file_path = 'mapillary_images_with_orientation/metadata.csv'
metadata = pd.read_csv(csv_file_path)

# Create a map centered at the average coordinates
avg_latitude = metadata['lat'].mean()
avg_longitude = metadata['long'].mean()
map_center = [avg_latitude, avg_longitude]

# Initialize the map
mymap = folium.Map(location=map_center, zoom_start=15)

# Add markers for each image's GPS location with orientation
for index, row in metadata.iterrows():
    lat = row['lat']
    long = row['long']
    img_id = row['id']
    img_url = row['thumb_2048_url']
    angle = row['orientation']  # Assuming this is the compass angle
    
    # Circle with a bold arrow inside, rotating the arrow based on the angle
    icon_html = f"""
    <div style="
        position: relative;
        width: 30px;
        height: 30px;
        border-radius: 50%;
        background-color: blue;
        border: 1px solid white;
        text-align: center;
        line-height: 30px;
        ">
        <div style="
            transform: rotate({angle}deg);
            position: absolute;
            top: 50%;
            left: 50%;
            transform-origin: center;
            font-size: 20px;  /* Increased font size */
            font-weight: bold; /* Makes the arrow appear bolder */
            color: black;
            ">
            &#x21E7;  <!-- Thicker arrow character -->
        </div>
    </div>
    """

    # Add the marker with the custom circle + bold arrow icon
    folium.Marker(
        location=[lat, long],
        popup=f'<img src="{img_url}" width="200"><br>ID: {img_id}',
        icon=folium.DivIcon(html=icon_html)
    ).add_to(mymap)

# Display the map in the Jupyter Notebook
display(mymap)


In [13]:
import requests
import os
import csv
import json
# Define your access token and sequence ID
access_token = 'MLY|8196090173836012|99bcaed29312ec0d1c06b22447943d94'

sequence_id = 'iSmeaCYW4Twa3C7C6WxtQw'
url = "https://graph.mapillary.com/image_ids?sequence_id={}".format(sequence_id)
header = {'Authorization' : 'OAuth {}'.format(access_token)}
r = requests.get(url, headers=header)
data_sequence = r.json()

# Check if images are found in the sequence
if 'data' in data_sequence:
    print(f"Images found in sequence {sequence_id}: {len(data_sequence['data'])}")

    # Create a directory to save images if it doesn't exist
    os.makedirs('mapillary_sequence_images', exist_ok=True)

    # Prepare a CSV file to save image metadata
    csv_file_path = 'mapillary_sequence_images/metadata.csv'
    with open(csv_file_path, mode='w', newline='') as csv_file:
        fieldnames = ['id', 'thumb_2048_url', 'captured_at', 'sequence', 'lat', 'long', 'orientation']
        writer = csv.DictWriter(csv_file, fieldnames=fieldnames)
        writer.writeheader()

        for image in data_sequence['data']:
            # Fetch detailed information for each image
            url_image = metadata_endpoint + '/{}?fields=id,thumb_2048_url,captured_at,sequence,geometry,compass_angle'.format(image['id'])
            response_image = requests.get(url_image, headers=headers)
            data_image = response_image.json()

            # Print image data (for debugging)
            print(data_image)

            # Extract information
            img_id = data_image.get('id')
            img_url = data_image.get('thumb_2048_url')
            captured_at = data_image.get('captured_at')
            sequence = data_image.get('sequence')
            location = data_image.get('geometry')
            orientation = data_image.get('compass_angle')
            # Extract coordinates and orientation
            if location:
                coordinates = location.get('coordinates')
                if coordinates:
                    longitude = coordinates[0]
                    latitude = coordinates[1]
                else:
                    longitude = None
                    latitude = None

            else:
                longitude = None
                latitude = None

            # Save image metadata to CSV
            writer.writerow({
                'id': img_id,
                'thumb_2048_url': img_url,
                'captured_at': captured_at,
                'sequence': sequence,
                'lat': latitude,
                'long': longitude,
                'orientation': orientation  
            })

            # Download the image and save it to the local directory
            if img_url:
                img_response = requests.get(img_url)
                if img_response.status_code == 200:
                    img_filename = f'mapillary_sequence_images/{img_id}.jpg'
                    with open(img_filename, 'wb') as f:
                        f.write(img_response.content)
                    print(f'Downloaded {img_id}.jpg')
                else:
                    print(f'Failed to download image {img_id}.jpg')
            else:
                print(f'No URL found for image {img_id}')
else:
    print(f"No images found for sequence {sequence_id}.")


Images found in sequence iSmeaCYW4Twa3C7C6WxtQw: 631
{'id': '500759547633812', 'thumb_2048_url': 'https://scontent-ams2-1.xx.fbcdn.net/m1/v/t6/An9Wsc4g6rteuFUPeFCNItMTFJc7XH8Wb2fv89J2j0GG44rr4WBhybbcYpUepXIRNKJcjADexe6RnAxlJlM9VPan0sAHIsolI5HTll2s6wTIkAEpH2WJWjW_ITKoQ7GsWqsuOEPV-LHwgRHvBIYqIQ?stp=s2048x1536&ccb=10-5&oh=00_AYBEzk-3ou6QJVBOvPP5jnQcjE5pOfP3dnj3DOA00P4AaQ&oe=674194A8&_nc_sid=201bca', 'captured_at': 1435473812000, 'sequence': 'iSmeaCYW4Twa3C7C6WxtQw', 'geometry': {'type': 'Point', 'coordinates': [5.177645, 52.06839]}, 'compass_angle': 235}
Downloaded 500759547633812.jpg
{'id': '743030876384597', 'thumb_2048_url': 'https://scontent-ams2-1.xx.fbcdn.net/m1/v/t6/An_olfZkGx-nzqxBEovGwH3VbGyk4b9SyfY9l9hL6CLv5o5qh5hSvGBtkmUhpD0bd0MasligmfBMRhOVx5wDPDovGLDtr55FME2mK1IoWWoYd2vh8fDmRZ0sesyORk3ecWfZRjxDJaYLlMEtmhjJVQ?stp=s2048x1536&ccb=10-5&oh=00_AYDXZzGi-WL8eN9oEKCTFLpbGj1k9X-kXD5xAsY2uhjuMA&oe=6741B751&_nc_sid=201bca', 'captured_at': 1435473820000, 'sequence': 'iSmeaCYW4Twa3C7C6WxtQ

In [14]:
print(data_sequence)

{'data': [{'id': '500759547633812'}, {'id': '743030876384597'}, {'id': '842207969977213'}, {'id': '2508513292778120'}, {'id': '527336924953507'}, {'id': '155585396495678'}, {'id': '753518645362924'}, {'id': '503816067471739'}, {'id': '1224613231307375'}, {'id': '3541140012681541'}, {'id': '949269185818620'}, {'id': '214383076782134'}, {'id': '519586819054351'}, {'id': '489818912224683'}, {'id': '803191327273904'}, {'id': '154864286570228'}, {'id': '514272279937139'}, {'id': '573545660218096'}, {'id': '2431995553610438'}, {'id': '2898106020510278'}, {'id': '974756883268895'}, {'id': '1472072019803177'}, {'id': '1145994452492231'}, {'id': '304583527909069'}, {'id': '497158314812848'}, {'id': '174581457769239'}, {'id': '2669896486634409'}, {'id': '512624553441243'}, {'id': '466770967922397'}, {'id': '923031391830594'}, {'id': '167341371968923'}, {'id': '980374109438572'}, {'id': '306681647501171'}, {'id': '470181420756472'}, {'id': '914078616113668'}, {'id': '519603679069504'}, {'id': '45

In [15]:
import pandas as pd
import folium
from IPython.display import display

# Load the metadata from the CSV file
csv_file_path = 'mapillary_sequence_images/metadata.csv'
metadata = pd.read_csv(csv_file_path)

# Create a map centered at the average coordinates
avg_latitude = metadata['lat'].mean()
avg_longitude = metadata['long'].mean()
map_center = [avg_latitude, avg_longitude]

# Initialize the map
mymap = folium.Map(location=map_center, zoom_start=15)

# Add markers for each image's GPS location with orientation
for index, row in metadata.iterrows():
    lat = row['lat']
    long = row['long']
    img_id = row['id']
    img_url = row['thumb_2048_url']
    angle = row['orientation']  # Assuming this is the compass angle
    
    # Circle with a bold arrow inside, rotating the arrow based on the angle
    icon_html = f"""
    <div style="
        position: relative;
        width: 30px;
        height: 30px;
        border-radius: 50%;
        background-color: blue;
        border: 1px solid white;
        text-align: center;
        line-height: 30px;
        ">
        <div style="
            transform: rotate({angle}deg);
            position: absolute;
            top: 50%;
            left: 50%;
            transform-origin: center;
            font-size: 20px;  /* Increased font size */
            font-weight: bold; /* Makes the arrow appear bolder */
            color: black;
            ">
            &#x21E7;  <!-- Thicker arrow character -->
        </div>
    </div>
    """

    # Add the marker with the custom circle + bold arrow icon
    folium.Marker(
        location=[lat, long],
        popup=f'<img src="{img_url}" width="200"><br>ID: {img_id}',
        icon=folium.DivIcon(html=icon_html)
    ).add_to(mymap)

# Display the map in the Jupyter Notebook
display(mymap)
